# Lax-Friedrichs Scheme (1D)

References:
1. Animation in Jupyter notebook: http://louistiao.me/posts/notebooks/embedding-matplotlib-animations-in-jupyter-notebooks/
2. Time stamp animation: https://stackoverflow.com/questions/16512308/show-elapsed-timeframe-number-in-matplotlib
3. Wikiepdia Burgers' Equation: https://en.wikipedia.org/wiki/Burgers%27_equation

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import fsolve
from scipy import sparse
%matplotlib inline

A 1D problem. $u:[0,T] \times \mathbb{R} \rightarrow \mathbb{R}$,
$$ u_t + (f(u))_x = 0 \quad \text{in } [0,T] \times \mathbb{R}, $$
$$ u(0,x) = v(x) \quad \text{for } x \in \mathbb{R}. $$

For the inviscid 1D Burgers' equation, $f,v \in C^1(\mathbb{R})$,
$$ f(u) = \frac{1}{2} u^2,$$
$$ v(x) = \exp(-x^2).$$

The Lax-Friedrichs scheme for the above problem is
$$ U^{l+1}_j = \frac{1}{2} \left( U_{j+1}^l + U_{j-1}^l \right) - \frac{k}{2h}\left( f(U_{j+1}^l) - f(U_{j-1}^l) \right), \quad l,j \in \mathbb{Z}, l \geq 0, $$
$$ U_j^0 = v(x_j), \quad j \in \mathbb{Z}, $$
where $x_j = jh$, $h, k > 0$ denote the spatial and temporal step sizes respectively.

Finally, the exact solution to the Burger's equation is given implicitly as
$$ u(x,t) = v(x - ut). $$

In [2]:
# define function for the initial condition.
def v(xh):
    return np.exp(-xh**2)
    
# non-linear function of u.
def f(uh):
    return 0.5 * uh**2

# solver for the implicit exact solution
def u_ex(u,x,t):
    return u - np.exp(-(x - u*t)**2)
    
def lfscheme(t,xmin,xmax,h,k):
    # set number of time steps.
    l = np.floor(t/k)
    # set min step for grid.
    jmin = np.ceil(xmin/h)
    # set max step for grid.
    jmax = np.floor(xmax/h)
    
    # define extended grid.
    xh = h * np.arange(jmin-l,jmax+l+1)
    
    # get initial values.
    U = v(xh)

    # recursion for the Lax-Friedrichs scheme.
    while l > 0:
        U = 0.5 * (U[2:] + U[:-2]) - k / (2. * h) * (f(U[2:]) - f(U[:-2]))
        l -= 1

    return U

In [3]:
# space domain
xmin = -3.
xmax = 4.

# time
tmin = 0.
tmax = 3.

p = 8
N = 2.**p
h = 1./N
k = 0.5 * h

# temporal and spatial grids
xh = np.arange(xmin,xmax+h,h)
tk = np.linspace(tmin,tmax,240)

## Plots
Plot the animation of the numerical and exact solutions of the 1D Burgers' equation.

In [4]:
from matplotlib import animation, rc
# plt.rcParams['animation.ffmpeg_path'] = '/usr/bin/ffmpeg'
from IPython.display import HTML
%matplotlib inline

fig, ax = plt.subplots()
plt.close()

ax.set_xlim((-3, 4))
ax.set_ylim((-0.5, 1.4))
ax.set_xlabel('x')
ax.set_ylabel('U')

line1, = ax.plot([],[], lw=2)
line2, = ax.plot([],[], lw=2)

time_text = ax.text(0.05, 0.95,'',horizontalalignment='left',verticalalignment='top', transform=ax.transAxes)

U_ex = np.zeros((xh.shape[0]))

XH = np.repeat(xh.reshape(1,-1),240,axis=0)
TK = np.repeat(tk.reshape(-1,1),xh.shape[0],axis=1)
xx = XH - v(XH) * TK
U_EX = v(xx)

def init():
    line1.set_data([], [])
    line2.set_data([], [])
    time_text.set_text('0.')
    return line1,line2,time_text

def animate(i):
    t = tk[i]
    U = lfscheme(t,xmin,xmax,h,k)
    line1.set_data(xh,U)
    
    # characteristic method
    U_ex = v(xh)
    xx = xh + U_ex * t
    
    line2.set_data(xx, U_ex)
    time_text.set_text('time = %.2f' %t)
    return (line1,time_text)

anim = animation.FuncAnimation(fig, animate, init_func=init,
                               frames=240, interval=50, blit=True)

HTML(anim.to_jshtml())

## Errors
Determine the maximum error at a given time $t$ for different grid resolutions.

In [5]:
# pick one point in time to calculate the error.
t = 1.

ps = np.arange(3,11)
errs = np.zeros((ps.shape[0]))

for p in ps:
    N = 2.**p
    h = 1./N
    k = 0.5*h
    
    xh = np.arange(xmin,xmax+h,h)
    U_ex = np.zeros((xh.shape[0]))
    
    j = 0
    for x in xh:
        U_ex[j] = fsolve(u_ex,0,args=(x,t))
        j += 1
        
    U = lfscheme(t,xmin,xmax,h,k)
#    errs[p-3] = np.sqrt(np.sum((U-U_ex)**2) / xh.shape[0]) # L2-error
    errs[p-3] = np.max(np.abs(U-U_ex))
    
from tabulate import tabulate
table = np.hstack((ps.reshape(-1,1),errs.reshape(-1,1)))
table = tabulate(table, headers = ['p', 'max errors'])
print(table)

  p    max errors
---  ------------
  3     0.279779
  4     0.215765
  5     0.160184
  6     0.112458
  7     0.0744375
  8     0.0461618
  9     0.0268384
 10     0.014797
